In [ ]:
import cv2
import numpy as np
import open3d as o3d
import os
from IPython.display import Video, display

# ================================
# VIDEO PATH (LOCAL MACHINE)
# ================================
video_path = r"C:\Users\PMYLS\Downloads\slam_output.mp4"
assert os.path.exists(video_path), "Video file not found!"

# ================================
# CAMERA INTRINSICS (GENERIC)
# ================================
fx = fy = 800
cx = 320
cy = 240

K = np.array([
    [fx, 0, cx],
    [0, fy, cy],
    [0,  0,  1]
])

# ================================
# ORB + MATCHER
# ================================
orb = cv2.ORB_create(2000)
bf = cv2.BFMatcher(cv2.NORM_HAMMING, crossCheck=True)

# ================================
# VIDEO READER
# ================================
cap = cv2.VideoCapture(video_path)
ret, prev_frame = cap.read()
if not ret:
    raise RuntimeError("Could not read first frame")

h, w = prev_frame.shape[:2]

# ================================
# VIDEO WRITER (OUTPUT)
# ================================
out_path = "ar_output.mp4"
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter(out_path, fourcc, 20, (w, h))

prev_gray = cv2.cvtColor(prev_frame, cv2.COLOR_BGR2GRAY)
kp_prev, des_prev = orb.detectAndCompute(prev_gray, None)

# ================================
# POSE INIT
# ================================
R_f = np.eye(3)
t_f = np.zeros((3, 1))
poses = []

# ================================
# AR CUBE (3D)
# ================================
cube_3d = np.float32([
    [0,0,0], [0,0.2,0], [0.2,0.2,0], [0.2,0,0],
    [0,0,-0.2], [0,0.2,-0.2], [0.2,0.2,-0.2], [0.2,0,-0.2]
])

def draw_cube(img, pts):
    pts = pts.reshape(-1, 2)
    edges = [(0,1),(1,2),(2,3),(3,0),
             (4,5),(5,6),(6,7),(7,4),
             (0,4),(1,5),(2,6),(3,7)]
    for i, j in edges:
        cv2.line(img, tuple(pts[i]), tuple(pts[j]), (0,255,0), 2)

print("[INFO] Processing video...")

# ================================
# MAIN LOOP
# ================================
while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    kp_curr, des_curr = orb.detectAndCompute(gray, None)

    if des_prev is None or des_curr is None:
        out.write(frame)
        continue

    matches = bf.match(des_prev, des_curr)
    matches = sorted(matches, key=lambda x: x.distance)

    if len(matches) < 8:
        out.write(frame)
        continue

    pts_prev = np.float32([kp_prev[m.queryIdx].pt for m in matches])
    pts_curr = np.float32([kp_curr[m.trainIdx].pt for m in matches])

    E, _ = cv2.findEssentialMat(
        pts_curr, pts_prev, K,
        cv2.RANSAC, 0.999, 1.0
    )

    if E is None:
        out.write(frame)
        continue

    _, R, t, _ = cv2.recoverPose(E, pts_curr, pts_prev, K)

    # ACCUMULATE POSE
    t_f += R_f @ t
    R_f = R @ R_f

    pose = np.eye(4)
    pose[:3, :3] = R_f
    pose[:3, 3] = t_f.flatten()
    poses.append(pose)

    # AR CUBE
    rvec, _ = cv2.Rodrigues(R_f)
    imgpts, _ = cv2.projectPoints(cube_3d, rvec, t_f, K, None)
    draw_cube(frame, imgpts.astype(int))

    # FEATURE POINTS
    for pt in pts_curr[:40]:
        cv2.circle(frame, tuple(pt.astype(int)), 2, (0,0,255), -1)

    out.write(frame)

    prev_gray = gray
    kp_prev = kp_curr
    des_prev = des_curr

cap.release()
out.release()

print("[INFO] Saved:", out_path)

# ================================
# DISPLAY OUTPUT VIDEO INLINE
# ================================
display(Video(out_path, embed=True))

# ================================
# OPEN3D TRAJECTORY
# ================================
print("[INFO] Visualizing 3D trajectory")

points, lines = [], []
for i in range(len(poses)):
    points.append(poses[i][:3, 3])
    if i > 0:
        lines.append([i-1, i])

line_set = o3d.geometry.LineSet(
    points=o3d.utility.Vector3dVector(points),
    lines=o3d.utility.Vector2iVector(lines)
)

o3d.visualization.draw_geometries([line_set])


Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
[INFO] Processing video...
[INFO] Saved: ar_output.mp4
